In [1]:
%cd ../..

/ibex/user/slimhy/Shape2VecSet/code


/home/slimhy/conda/envs/shape2vecset/lib/python3.10/site-packages/IPython/core/magics/osm.py:417: UserWarning: using dhist requires you to install the `pickleshare` library.
  self.shell.db['dhist'] = compress_dhist(dhist)[-100:]


In [3]:
!ls

chamfer3D	      __init__.py	  models_class_cond.py
engine_ae.py	      jupyter		  output
engine_class_cond.py  losses		  plot_pc.py
engine_listener.py    main_ae.py	  __pycache__
engine_node2node.py   main_class_cond.py  sample_class_cond.py
eval.py		      main_node2node.py   tmp
extract_features.py   models		  util


In [7]:
import mcubes
import numpy as np
import os
import torch
import trimesh
from models.imnet import IMNetAE


def load_imnet():
    if torch.cuda.is_available():
        device = torch.device("cuda")
        torch.backends.cudnn.benchmark = True
    else:
        device = torch.device("cpu")

    imnet = IMNetAE(sample_vox_size=64, device=device)

    # Load checkpoint
    ckpt_path = "/ibex/user/slimhy/Shape2VecSet/output/imnet/imnet_ckpt.pth"
    imnet.IMNet.load_state_dict(torch.load(ckpt_path))

    return imnet


def infer_voxels(imnet, voxels):
    imnet.IMNet = imnet.IMNet.eval()
    batch_voxels_ = voxels.astype(np.float32)
    batch_voxels = torch.from_numpy(batch_voxels_)
    batch_voxels = batch_voxels.to(imnet.device)
    model_z, _ = imnet.IMNet(batch_voxels)
    return imnet.z2voxel(model_z), model_z


def pred_mesh(imnet, voxels, optimize_mesh=False):
    model_float, model_z = infer_voxels(imnet, voxels)

    vertices, triangles = mcubes.marching_cubes(
        model_float, imnet.sampling_threshold
    )
    vertices = (vertices.astype(np.float32) - 0.5) / imnet.real_size - 0.5
    if optimize_mesh:
        vertices = imnet.optimize_mesh(vertices, model_z)

    # Load in trimesh from vertices and triangles
    mesh = trimesh.Trimesh(vertices, triangles)

    return mesh

imnet = load_imnet()

In [8]:
test_voxels = np.load("/ibex/user/slimhy/ShapeWalk/voxels/1522051158219049366.npy")
test_voxels = np.unpackbits(test_voxels, axis=-1)
test_voxels = np.expand_dims(test_voxels, axis=0)
pred_mesh(imnet, test_voxels).show()